In [249]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from support import fama_french
from fredapi import Fred
import quandl as q
from IPython.display import Image
fred = Fred(api_key="11ae3d2ef9363b6c65ce74df68755758")
plt.style.use("ggplot")

In [319]:
yields = q.get("USTREASURY/YIELD")
yields.columns.name = "Maturities"
print(yields.head().to_latex())

\begin{tabular}{lrrrrrrrrrrrr}
\toprule
Maturities &  1 MO &  2 MO &  3 MO &  6 MO &  1 YR &  2 YR &  3 YR &  5 YR &  7 YR &  10 YR &  20 YR &  30 YR \\
Date       &       &       &       &       &       &       &       &       &       &        &        &        \\
\midrule
1990-01-02 &   NaN &   NaN &  7.83 &  7.89 &  7.81 &  7.87 &  7.90 &  7.87 &  7.98 &   7.94 &    NaN &   8.00 \\
1990-01-03 &   NaN &   NaN &  7.89 &  7.94 &  7.85 &  7.94 &  7.96 &  7.92 &  8.04 &   7.99 &    NaN &   8.04 \\
1990-01-04 &   NaN &   NaN &  7.84 &  7.90 &  7.82 &  7.92 &  7.93 &  7.91 &  8.02 &   7.98 &    NaN &   8.04 \\
1990-01-05 &   NaN &   NaN &  7.79 &  7.85 &  7.79 &  7.90 &  7.94 &  7.92 &  8.03 &   7.99 &    NaN &   8.06 \\
1990-01-08 &   NaN &   NaN &  7.79 &  7.88 &  7.81 &  7.90 &  7.95 &  7.92 &  8.05 &   8.02 &    NaN &   8.09 \\
\bottomrule
\end{tabular}



/var/folders/wh/63dtvrx97_31k2y9clt5xgwc0000gn/T/ipykernel_18408/3673553976.py:3: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.



In [323]:
print(yields.head().style.to_latex())

\begin{tabular}{lrrrrrrrrrrrr}
Maturities & 1 MO & 2 MO & 3 MO & 6 MO & 1 YR & 2 YR & 3 YR & 5 YR & 7 YR & 10 YR & 20 YR & 30 YR \\
Date &  &  &  &  &  &  &  &  &  &  &  &  \\
1990-01-02 00:00:00 & nan & nan & 7.830000 & 7.890000 & 7.810000 & 7.870000 & 7.900000 & 7.870000 & 7.980000 & 7.940000 & nan & 8.000000 \\
1990-01-03 00:00:00 & nan & nan & 7.890000 & 7.940000 & 7.850000 & 7.940000 & 7.960000 & 7.920000 & 8.040000 & 7.990000 & nan & 8.040000 \\
1990-01-04 00:00:00 & nan & nan & 7.840000 & 7.900000 & 7.820000 & 7.920000 & 7.930000 & 7.910000 & 8.020000 & 7.980000 & nan & 8.040000 \\
1990-01-05 00:00:00 & nan & nan & 7.790000 & 7.850000 & 7.790000 & 7.900000 & 7.940000 & 7.920000 & 8.030000 & 7.990000 & nan & 8.060000 \\
1990-01-08 00:00:00 & nan & nan & 7.790000 & 7.880000 & 7.810000 & 7.900000 & 7.950000 & 7.920000 & 8.050000 & 8.020000 & nan & 8.090000 \\
\end{tabular}



In [247]:
# Monthly
# yields = q.get("USTREASURY/YIELD", collapse="monthly")
# yields.index = yields.index + pd.offsets.MonthBegin(-1)

# Daily
yields = q.get("USTREASURY/YIELD")
yields.columns = [1/12, 2/12, 3/12, 6/12, 1, 2, 3, 5, 7, 10, 20, 30]

today = yields.loc["2022-11-10"]
yearago = yields.loc["2021-11-10"]
inverted = yields.loc["2007-03-01"]
normal = yields.loc["2019-06-27"]
# flat = yields.loc["2020-01-03"]
flat = yields.loc["2007-06-15"]
# increasing = yields.loc["2014-06-16"]
increasing = yields.loc["1992-10-30"]

examples = pd.concat([today, yearago, inverted, normal, flat, increasing], axis=1)

examples.columns = [
    f"Today {today.name.strftime('%m/%d/%Y')}",
    f"Year Ago {yearago.name.strftime('%m/%d/%Y')}",
    f"Inverted {inverted.name.strftime('%m/%d/%Y')}",
    f"Normal {normal.name.strftime('%m/%d/%Y')}",
    f"Flat {flat.name.strftime('%m/%d/%Y')}",
    f"Increasing {increasing.name.strftime('%m/%d/%Y')}"
]

px.line(examples, title="Examples of Yield Curve Shapes", labels={'index':'Maturity in Years', 'value':'Percent', 'variable':'Shapes'})

In [305]:
fig = go.Figure()
for i in examples.columns.to_list():
    fig.add_trace(go.Scatter(x=examples.index, y=examples[i], mode='lines', name=i, connectgaps=True))

fig.update_layout(
    title="Plot Title",
    # xaxis_title="X Axis Title",
    # yaxis_title="Y Axis Title",
    # legend_title="Legend Title",
    font=dict(
        size=18,
        color="Black"
    )
)

fig.show()

In [315]:
fig = go.Figure(layout={"width":900, "height":500})
for i in examples.columns.to_list():
    fig.add_trace(go.Scatter(x=examples.index, y=examples[i], mode='lines', name=i, connectgaps=True))

fig.update_layout(
    xaxis_title="Maturity in Years",
    yaxis_title="Percent",
    legend_title="Shapes",
    xaxis=dict(
        showline=True,
        showgrid=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    yaxis=dict(
        showgrid=True,
        zeroline=True,
        showline=True,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    autosize=True,
    margin=dict(
        autoexpand=True,
        l=80,
        r=20,
        t=110,
    ),
    showlegend=True,
    plot_bgcolor='white'
)

annotations = []
# Title
annotations.append(dict(xref='paper', yref='paper', x=0.5, y=1.15,
                              xanchor='center', yanchor='bottom',
                              text='Examples of Yield Curve Shapes',
                              font=dict(family='Arial',
                                        size=30,
                                        color='rgb(37,37,37)'),
                              showarrow=False))
# Source
annotations.append(dict(xref='paper', yref='paper', x=0.5, y=-0.2,
                              xanchor='center', yanchor='top',
                              text='Source: Nasdaq Data Link. ' +
                                   'Accessed via Quandl on 11/29/2022 ',
                              font=dict(family='Arial',
                                        size=12,
                                        color='rgb(150,150,150)'),
                              showarrow=False))

fig.update_layout(annotations=annotations)

fig.show()

In [239]:
inverted.index.min().strftime('%m/%d/%Y')

AttributeError: 'numpy.float64' object has no attribute 'strftime'

In [230]:
# yields.loc["2019":].T.plot(figsize=(16, 10))
px.line(yields.loc["2020"].T)

/Users/wyattnechtman/miniforge3/lib/python3.9/site-packages/plotly/express/_core.py:1222: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/Users/wyattnechtman/miniforge3/lib/python3.9/site-packages/plotly/express/_core.py:1222: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/Users/wyattnechtman/miniforge3/lib/python3.9/site-packages/plotly/express/_core.py:1222: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all col

### A dynamic factor model of the yield curve components as a predictor of the economy
Marcelle Chauvet and Zeynep Senyuz

"The series on US Treasury yields with maturities of three months, two years, and ten years are used to construct empirical proxies of the level, curvature, and slope of the yield curve."

Their data is 08/1971 - 12/2012

In [37]:
# Focus on 3M, 2Y, and 10Y to reconstruct level, slope, and curvature.
yields = yields[["3 MO", "2 YR", "10 YR"]]
print(yields.info())
yields.head()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 8233 entries, 1990-01-02 to 2022-11-25
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   3 MO    8230 non-null   float64
 1   2 YR    8233 non-null   float64
 2   10 YR   8233 non-null   float64
dtypes: float64(3)
memory usage: 257.3 KB
None


3 MO  2 YR  10 YR
Date                         
1990-01-02  7.83  7.87   7.94
1990-01-03  7.89  7.94   7.99
1990-01-04  7.84  7.92   7.98
1990-01-05  7.79  7.90   7.99
1990-01-08  7.79  7.90   8.02

### Why do we have so many 3 month data series?

#### What Is Bank Discount Basis?
[Bank discount basis](https://www.investopedia.com/terms/b/bankdiscountbasis.asp), also known as discount yield, is a convention used by financial institutions when quoting prices for fixed-income securities sold at a discount, such as municipal and U.S. Treasury bills. The quote is presented as a percentage of face value and is determined by discounting the bond by using a 360-day-count convention, which assumes there are twelve 30-day months in a year.

In [179]:
data = pd.read_csv("../Data/feds200628.csv", skiprows=8)
data["Date"] = pd.to_datetime(data["Date"])
data.set_index("Date", inplace=True)
# Zero Coupon Yield
# zcy = data[[i for i in data.columns.to_list() if "SVENY" in i]]
# Par Yield
# py = data[[i for i in data.columns.to_list() if "SVENPY" in i]]

# data
# pd.merge(zcy[["SVENY03"]], py[["SVENPY03"]], left_index=True, right_index=True)
data[["SVENY03", "SVENPY03"]]

SVENY03  SVENPY03
Date                         
1961-06-14   3.5530    3.5724
1961-06-15   3.5981    3.6175
1961-06-16   3.5994    3.6188
1961-06-19   3.6252    3.6446
1961-06-20   3.5986    3.6178
...             ...       ...
2022-11-14   4.2129    4.2689
2022-11-15   4.1499    4.2054
2022-11-16   4.0942    4.1500
2022-11-17   4.1889    4.2461
2022-11-18   4.2507    4.3091

[16028 rows x 2 columns]

In [193]:
dgs3mo = fred.get_series('DGS3MO')
# dgs3mo.name = "Investment Basis"
dgs3mo.name = "DGS3MO"

dtb3 = fred.get_series('DTB3')
# dtb3.name = "Discount Basis"
dtb3.name = "DTB3"

c = pd.merge(dgs3mo, dtb3, left_index=True, right_index=True, how='outer')
c.index.name = "Date"
c.columns.name = "Percent"
c = pd.merge(c, data[["SVENY03", "SVENPY03"]], left_index=True, right_index=True, how='outer')
# c["Spread"] = c["Investment Basis"] - c["Discount Basis"]

t1 = f"DGS3MO: Market Yield on U.S. Treasury Securities at 3-Month Constant Maturity, Quoted on an Investment Basis, {dgs3mo.index.min().strftime('%m/%d/%Y')} - {dgs3mo.index.max().strftime('%m/%d/%Y')}"
t2 = f"DTB3: 3-Month Treasury Bill Secondary Market Rate, Discount Basis, {dtb3.index.min().strftime('%m/%d/%Y')} - {dtb3.index.max().strftime('%m/%d/%Y')}"
t3 = f"SVENY03: Nominal Zero-Coupon Yield, {data.index.min().strftime('%m/%d/%Y')} - {data.index.max().strftime('%m/%d/%Y')}"
t4 = f"SVENPY03: Nominal Par Yield, {data.index.min().strftime('%m/%d/%Y')} - {data.index.max().strftime('%m/%d/%Y')}"
print(t1 + "\nvs.\n" + t2 + "\nvs.\n" + t3 + "\nvs.\n" + t4)
# title_ = "3-Month Treasuries Quoted on Investment Basis (DGS3MO), Discount Basis (DTB3), (SVENY03) Nominal Zero-Coupon Yield, (SVENPY03) Nominal Par Yield"
title_ = "3-Month Treasuries"
fig = px.line(c, title=title_, labels={'value':'Percent'}, width=1200, height=600)
fig.show()
c.describe()

DGS3MO: Market Yield on U.S. Treasury Securities at 3-Month Constant Maturity, Quoted on an Investment Basis, 09/01/1981 - 11/25/2022
vs.
DTB3: 3-Month Treasury Bill Secondary Market Rate, Discount Basis, 01/04/1954 - 11/25/2022
vs.
SVENY03: Nominal Zero-Coupon Yield, 06/14/1961 - 11/18/2022
vs.
SVENPY03: Nominal Par Yield, 06/14/1961 - 11/18/2022


DGS3MO          DTB3       SVENY03      SVENPY03
count  10309.000000  17217.000000  15323.000000  15323.000000
mean       3.750913      4.171795      5.217202      5.300348
std        3.232285      3.121542      3.205850      3.302470
min        0.000000     -0.050000      0.127200      0.127200
25%        0.520000      1.710000      2.677550      2.687800
50%        3.490000      3.940000      5.221800      5.271500
75%        5.750000      5.740000      7.186822      7.293050
max       17.010000     17.140000     15.574600     16.223500

In [194]:
dgs3mo = fred.get_series('DGS3MO')
dgs3mo.name = "InvestmentBasis"
# dgs3mo.name = "dgs3mo"

dtb3 = fred.get_series('DTB3')
dtb3.name = "DiscountBasis"
# dtb3.name = "dtb3"

# c = pd.merge(dgs3mo, dtb3, left_index=True, right_index=True)
c = pd.DataFrame(dgs3mo).join(pd.DataFrame(dtb3), how='outer')
c.index.name = "Date"
c.columns.name = "Percent"


t1 = f"DGS3MO: Market Yield on U.S. Treasury Securities at 3-Month Constant Maturity, Quoted on an Investment Basis, {dgs3mo.index.min().strftime('%m/%d/%Y')} - {dgs3mo.index.max().strftime('%m/%d/%Y')}"
t2 = f"DTB3: 3-Month Treasury Bill Secondary Market Rate, Discount Basis, {dtb3.index.min().strftime('%m/%d/%Y')} - {dtb3.index.max().strftime('%m/%d/%Y')}"
# t3 = "DTB3: 3-Month Treasury Bill Secondary Market Rate, Discount Basis"
# print(t1 + "\nvs.\n" + t2 + "\nvs.\n" + t3)
print(t1 + "\nvs.\n" + t2)
fig = px.line(c, title="DGS3MO compared to DTB3", labels={'x':'Date', 'y':'Percent'}, width=1200, height=600)
fig.show()
c.describe()

DGS3MO: Market Yield on U.S. Treasury Securities at 3-Month Constant Maturity, Quoted on an Investment Basis, 09/01/1981 - 11/25/2022
vs.
DTB3: 3-Month Treasury Bill Secondary Market Rate, Discount Basis, 01/04/1954 - 11/25/2022


Percent  InvestmentBasis  DiscountBasis
count       10309.000000   17217.000000
mean            3.750913       4.171795
std             3.232285       3.121542
min             0.000000      -0.050000
25%             0.520000       1.710000
50%             3.490000       3.940000
75%             5.750000       5.740000
max            17.010000      17.140000

"Monthly yields are obtained by taking averages of daily yields."

In [209]:
# TB3MS: 3-Month Treasury Bill Secondary Market Rate, Discount Basis (MONTHLY)
# m3name = "TB3MS"

# DTB3: 3-Month Treasury Bill Secondary Market Rate, Discount Basis 
# m3name = "DTB3"

# DGS3MO: Market Yield on U.S. Treasury Securities at 3-Month Constant Maturity, Quoted on an Investment Basis
m3name = "DGS3MO"
m3 = fred.get_series(m3name)
m3.name = m3name

y2name = "DGS2"
y2 = fred.get_series(y2name)
y2.name = y2name

y10name = "DGS10"
y10 = fred.get_series(y10name)
y10.name = y10name

myields = pd.merge(
    pd.merge(
        m3,
        y2,
        left_index=True,
        right_index=True,
        how='outer'
    ),
    y10,
    left_index=True,
    right_index=True,
    how='outer'
)

# Group Quandl Data
# myields = yields.groupby(pd.Grouper(freq='M')).mean()

myields = myields.groupby(pd.Grouper(freq='M')).mean()
myields.columns = ["3M", "2Y", "10Y"]
# myields.dropna(thresh=2)
myields

3M        2Y       10Y
1962-01-31       NaN       NaN  4.083182
1962-02-28       NaN       NaN  4.039444
1962-03-31       NaN       NaN  3.930455
1962-04-30       NaN       NaN  3.843000
1962-05-31       NaN       NaN  3.873636
...              ...       ...       ...
2022-07-31  2.298000  3.036000  2.896000
2022-08-31  2.721739  3.250000  2.897826
2022-09-30  3.221905  3.856667  3.519048
2022-10-31  3.872500  4.375000  3.983500
2022-11-30  4.311765  4.514706  3.923529

[731 rows x 3 columns]

In [211]:
myields.loc["1971":]

3M        2Y       10Y
1971-01-31       NaN       NaN  6.238500
1971-02-28       NaN       NaN  6.112222
1971-03-31       NaN       NaN  5.703478
1971-04-30       NaN       NaN  5.833810
1971-05-31       NaN       NaN  6.392500
...              ...       ...       ...
2022-07-31  2.298000  3.036000  2.896000
2022-08-31  2.721739  3.250000  2.897826
2022-09-30  3.221905  3.856667  3.519048
2022-10-31  3.872500  4.375000  3.983500
2022-11-30  4.311765  4.514706  3.923529

[623 rows x 3 columns]

"The empirical proxies used to represent the level, slope, and curvature of the yield curve are then constructed as follows: the level factor ($L_t$) is computed as the average of the 3-month, 2-year, and 10-year bond yields; the curvature ($C_t$) is measured as twice the 2-year bond yield minus the sum of the 3-month and 10-year bond yields; and the slope of the yield curve ($T_t$) corresponds to the difference between the 10-year bond rate and the 3-month T-bill rate."

In [324]:
# Level: average of 3M, 2Y, and 10Y
# level = myields.T.mean()
level = myields.mean(axis=1)
level.name = "Level"

# Curvature: twice the 2Y minus the sum of 3M and 10Y
# curvature = 2 * myields["2 YR"] - (myields["3 MO"] + myields["10 YR"])
curvature = 2 * myields["2Y"] - (myields["3M"] + myields["10Y"])
curvature.name = "Curvature"

# Slope: difference between 10Y and 3M
slope = myields["10Y"] - myields["3M"]
slope.name = "Slope"

factors = pd.concat([level, slope, curvature], axis=1)
factors.dropna(thresh=2, inplace=True)

# Dates of U.S. recessions as inferred by GDP-based recession indicator
var = "JHDUSRGDPBR"
rec = pd.DataFrame(fred.get_series(var), columns=["Rec"])

start_rec = [i.strftime("%Y-%m-%d") for i in rec[(rec["Rec"] == 1) & (rec["Rec"].shift(1) == 0) & (rec["Rec"].shift(-1) == 1)].index.date]
end_rec = [i.strftime("%Y-%m-%d") for i in rec[(rec["Rec"] == 1) & (rec["Rec"].shift(-1) == 0) & (rec["Rec"].shift(1) == 1)].index.date]

fig = px.line(factors, title="Level, Slope, and Curvature with Shaded Recession", width=1200, height=600, labels={'value':'Percent', 'variable':'Factor', 'index':'Date'})
for start, end in zip(start_rec, end_rec):
    if pd.to_datetime(end) > factors.index.min():
        fig.add_vrect(x0=start, x1=end, fillcolor="grey", opacity=0.5, line_width=0)
fig.show()


Compare to figure from Chauvet

![alternative text](../Figures/f1_chauvet03.png "Figure 1 Chauvet")

Looks pretty similar!

#### Zero Coupon vs. Par Yield?
A [Par Yield Curve](https://www.investopedia.com/terms/p/par-yield-curve.asp) is a graphical representation of the yields of hypothetical Treasury securities with prices at par. On the par yield curve, the coupon rate will equal the yield to maturity (YTM) of the security, which is why the Treasury bond will trade at par.

The [par yield curve](https://www.quora.com/What-is-the-difference-between-a-yield-curve-and-a-par-curve) gives the coupon rate of a theoretical bond that would sell at par for the given maturity. The zero coupon curve gives the yield of a theoretical zero-coupon bond. Without a modifier, a yield curve is usually assumed to be a par curve.

In [91]:
# Zero-coupon yield: continuously compounded SVENYXX
# Par yield: coupon-equivalent SVENPYXX
# Instantaneous forward rate: continuously compounded SVENFXX
# One-year forward rate: coupon-equivalent SVEN1FXX
# Parameters: BETA0 - TAU2

# Can't read online?
# pd.read_csv("https://www.federalreserve.gov/data/yield-curve-tables/feds200628.csv", skiprows=8)
data = pd.read_csv("../Data/feds200628.csv", skiprows=8)
data["Date"] = pd.to_datetime(data["Date"])
data.set_index("Date", inplace=True)
data.head()

BETA0     BETA1     BETA2  BETA3  SVEN1F01  SVEN1F04  SVEN1F09  \
Date                                                                            
1961-06-14  3.917606 -1.277955 -1.949397    0.0    3.8067    3.9562       NaN   
1961-06-15  3.978498 -1.257404 -2.247617    0.0    3.8694    4.0183       NaN   
1961-06-16  3.984350 -1.429538 -1.885024    0.0    3.8634    4.0242       NaN   
1961-06-19  4.004379 -0.723311 -3.310743    0.0    3.9196    4.0447       NaN   
1961-06-20  3.985789 -0.900432 -2.844809    0.0    3.8732    4.0257       NaN   

            SVENF01  SVENF02  SVENF03  ...  SVENY23  SVENY24  SVENY25  \
Date                                   ...                              
1961-06-14   3.5492   3.8825   3.9149  ...      NaN      NaN      NaN   
1961-06-15   3.5997   3.9460   3.9763  ...      NaN      NaN      NaN   
1961-06-16   3.5957   3.9448   3.9811  ...      NaN      NaN      NaN   
1961-06-19   3.6447   3.9842   4.0035  ...      NaN      NaN      NaN   
1961-06-20   3.5845   3.9552   3.9840  ...      NaN      NaN      NaN   

            SVENY26  SVENY27  SVENY28  SVENY29  SVENY30      TAU1    TAU2  
Date                                                                       
1961-06-14      NaN      NaN      NaN      NaN      NaN  0.339218 -999.99  
1961-06-15      NaN      NaN      NaN      NaN      NaN  0.325775 -999.99  
1961-06-16      NaN      NaN      NaN      NaN      NaN  0.348817 -999.99  
1961-06-19      NaN      NaN      NaN      NaN      NaN  0.282087 -999.99  
1961-06-20      NaN      NaN      NaN      NaN      NaN  0.310316 -999.99  

[5 rows x 99 columns]

#### Nelson-Siegel
$$
f_t(n, 0) = \beta_0 + \beta_1 \exp(-n/\tau_1) + \beta_2 (n/\tau_1) \exp(-n/\tau_1) 
$$

#### Nelson-Siegel-Svensson
$$
f_t(n, 0) = \beta_0 + \beta_1 \exp(-n/\tau_1) + \beta_2 (n/\tau_1) \exp(-n/\tau_1) + \beta_3 (n/\tau_2) \exp(-n/\tau_2) 
$$

In [214]:
# Backout 3-month
# data.apply(lambda b0, b1, b2, t1, t2)
def nelson_siegel(n, beta0, beta1, beta2, tau1):
    return beta0 + (beta1 * np.exp(-n / tau1)) + (beta2 * (n / tau1) * np.exp(-n / tau1))

three_months = 3 / 12

three_m = data.apply(lambda x: nelson_siegel(three_months, x["BETA0"], x["BETA1"], x["BETA2"], x["TAU1"]), axis=1)
three_m.name = "3M NS"

tmp = pd.merge(yields["3 MO"], three_m, left_index=True, right_index=True, how='left').round(2)
tmp["Diff"] = tmp["3 MO"] - tmp["3M NS"]
display(tmp.head())
# tmp["Diff"].describe()
print(tmp.describe())
px.line(tmp[["3 MO", "3M NS"]], title="3 Month Yield: Nelson-Siegel Fit vs. Actual")

3 MO  3M NS  Diff
Date                         
1990-01-02  7.83   7.82  0.01
1990-01-03  7.89   7.87  0.02
1990-01-04  7.84   7.91 -0.07
1990-01-05  7.79   7.81 -0.02
1990-01-08  7.79   7.78  0.01

              3 MO         3M NS          Diff
count  8230.000000   8208.000000   8205.000000
mean      2.596265    -22.951691     25.550280
std       2.284158    465.574677    465.506074
min       0.000000 -20635.970000   -848.480000
25%       0.162500      0.307500     -0.260000
50%       2.070000      2.260000     -0.010000
75%       4.880000      5.160000      0.220000
max       8.260000    850.890000  20635.990000


In [100]:
# Zero-coupon yield
zcy = data[[i for i in data.columns.to_list() if "SVENY" in i]]
print("Zero-coupon yield")
display(zcy.head())

# Par yield
py = data[[i for i in data.columns.to_list() if "SVENPY" in i]]
print("Par yield")
display(py.head())

# Instantaneous forward rate
ifr = data[[i for i in data.columns.to_list() if "SVENF" in i]]
print("Instantaneous forward rate")
display(ifr.head())

# One-year forward rate
ofr = data[[i for i in data.columns.to_list() if "SVEN1F" in i]]
print("One-year forward rate")
display(ofr.head())

# Parameters
params = data[[i for i in data.columns.to_list() if ("BETA" in i) or ("TAU" in i)]]
print("Parameters")
display(params.head())

Zero-coupon yield


SVENY01  SVENY02  SVENY03  SVENY04  SVENY05  SVENY06  SVENY07  \
Date                                                                        
1961-06-14   2.9825   3.3771   3.5530   3.6439   3.6987   3.7351   3.7612   
1961-06-15   2.9941   3.4137   3.5981   3.6930   3.7501   3.7882   3.8154   
1961-06-16   3.0012   3.4142   3.5994   3.6953   3.7531   3.7917   3.8192   
1961-06-19   2.9949   3.4386   3.6252   3.7199   3.7768   3.8147   3.8418   
1961-06-20   2.9833   3.4101   3.5986   3.6952   3.7533   3.7921   3.8198   

            SVENY08  SVENY09  SVENY10  ...  SVENY21  SVENY22  SVENY23  \
Date                                   ...                              
1961-06-14      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-15      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-16      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-19      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-20      NaN      NaN      NaN  ...      NaN      NaN      NaN   

            SVENY24  SVENY25  SVENY26  SVENY27  SVENY28  SVENY29  SVENY30  
Date                                                                       
1961-06-14      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-15      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-16      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-19      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-20      NaN      NaN      NaN      NaN      NaN      NaN      NaN  

[5 rows x 30 columns]

Par yield


SVENPY01  SVENPY02  SVENPY03  SVENPY04  SVENPY05  SVENPY06  \
Date                                                                     
1961-06-14    3.0025    3.3973    3.5724    3.6627    3.7169    3.7530   
1961-06-15    3.0141    3.4339    3.6175    3.7117    3.7683    3.8060   
1961-06-16    3.0213    3.4346    3.6188    3.7140    3.7713    3.8094   
1961-06-19    3.0150    3.4589    3.6446    3.7387    3.7951    3.8327   
1961-06-20    3.0034    3.4303    3.6178    3.7137    3.7713    3.8096   

            SVENPY07  SVENPY08  SVENPY09  SVENPY10  ...  SVENPY21  SVENPY22  \
Date                                                ...                       
1961-06-14    3.7787       NaN       NaN       NaN  ...       NaN       NaN   
1961-06-15    3.8328       NaN       NaN       NaN  ...       NaN       NaN   
1961-06-16    3.8365       NaN       NaN       NaN  ...       NaN       NaN   
1961-06-19    3.8595       NaN       NaN       NaN  ...       NaN       NaN   
1961-06-20    3.8370       NaN       NaN       NaN  ...       NaN       NaN   

            SVENPY23  SVENPY24  SVENPY25  SVENPY26  SVENPY27  SVENPY28  \
Date                                                                     
1961-06-14       NaN       NaN       NaN       NaN       NaN       NaN   
1961-06-15       NaN       NaN       NaN       NaN       NaN       NaN   
1961-06-16       NaN       NaN       NaN       NaN       NaN       NaN   
1961-06-19       NaN       NaN       NaN       NaN       NaN       NaN   
1961-06-20       NaN       NaN       NaN       NaN       NaN       NaN   

            SVENPY29  SVENPY30  
Date                            
1961-06-14       NaN       NaN  
1961-06-15       NaN       NaN  
1961-06-16       NaN       NaN  
1961-06-19       NaN       NaN  
1961-06-20       NaN       NaN  

[5 rows x 30 columns]

Instantaneous forward rate


SVENF01  SVENF02  SVENF03  SVENF04  SVENF05  SVENF06  SVENF07  \
Date                                                                        
1961-06-14   3.5492   3.8825   3.9149   3.9174   3.9176   3.9176   3.9176   
1961-06-15   3.5997   3.9460   3.9763   3.9784   3.9785   3.9785   3.9785   
1961-06-16   3.5957   3.9448   3.9811   3.9841   3.9843   3.9843   3.9844   
1961-06-19   3.6447   3.9842   4.0035   4.0043   4.0044   4.0044   4.0044   
1961-06-20   3.5845   3.9552   3.9840   3.9857   3.9858   3.9858   3.9858   

            SVENF08  SVENF09  SVENF10  ...  SVENF21  SVENF22  SVENF23  \
Date                                   ...                              
1961-06-14      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-15      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-16      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-19      NaN      NaN      NaN  ...      NaN      NaN      NaN   
1961-06-20      NaN      NaN      NaN  ...      NaN      NaN      NaN   

            SVENF24  SVENF25  SVENF26  SVENF27  SVENF28  SVENF29  SVENF30  
Date                                                                       
1961-06-14      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-15      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-16      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-19      NaN      NaN      NaN      NaN      NaN      NaN      NaN  
1961-06-20      NaN      NaN      NaN      NaN      NaN      NaN      NaN  

[5 rows x 30 columns]

One-year forward rate


SVEN1F01  SVEN1F04  SVEN1F09
Date                                    
1961-06-14    3.8067    3.9562       NaN
1961-06-15    3.8694    4.0183       NaN
1961-06-16    3.8634    4.0242       NaN
1961-06-19    3.9196    4.0447       NaN
1961-06-20    3.8732    4.0257       NaN

Parameters


BETA0     BETA1     BETA2  BETA3      TAU1    TAU2
Date                                                             
1961-06-14  3.917606 -1.277955 -1.949397    0.0  0.339218 -999.99
1961-06-15  3.978498 -1.257404 -2.247617    0.0  0.325775 -999.99
1961-06-16  3.984350 -1.429538 -1.885024    0.0  0.348817 -999.99
1961-06-19  4.004379 -0.723311 -3.310743    0.0  0.282087 -999.99
1961-06-20  3.985789 -0.900432 -2.844809    0.0  0.310316 -999.99